# IMPORTS E CONFIGURAÇÕES

In [1]:
# Import de bibliotecas
from zipfile import ZipFile  # Leitura de arquivos .zipgit 
import requests  # Requisição web
from io import BytesIO  # Leitura de arquivo em bytes
import numpy as np  # Manipulação de dados matriciais
import pandas as pd  # Manipulação de dados
import plotly.express as px  # Visualização gráfica
import plotly.graph_objects as go  # Visualização gráfica mais avançada



# Configurações das bibliotecas
pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.options.display.max_colwidth = None

# EXTRAÇÃO DOS DADOS

In [2]:
# Extrair o arquivo excel da pasta ZIP diretamente do site de download
url = 'https://www.b3.com.br/data/files/57/E6/AA/A1/68C7781064456178AC094EA8/ClassifSetorial.zip'
response = requests.get(url=url)
with ZipFile(BytesIO(response.content)) as fold:
    file = fold.namelist()[0]
    with fold.open(file) as file:
        df = pd.read_excel(io=file, skiprows=6)

# TRANSFORMAÇÃO DOS DADOS

In [3]:
# Renomeando as colunas necessárias
df = df.rename(columns={'SETOR ECONÔMICO': 'SETOR', 'SEGMENTO': 'NOME', 'LISTAGEM': 'CÓDIGO', 'Unnamed: 4': 'LISTAGEM'})[1:-18]
# Preenchendo valores nulos da coluna SEGMENTO com os valores da coluna NOME onde a coluna CÓDIGO FOR vazia
df.loc[(df['CÓDIGO'].isnull()), 'SEGMENTO'] = df.loc[(df['CÓDIGO'].isnull()), 'NOME']
# Removendo linhas com todos as variáveis nulas
df = df.dropna(how='all')
# Preenchendo valores nulos da coluna LISTAGEM com 'Sem classificação'
df.LISTAGEM = df.LISTAGEM.fillna(value='AUSENTE')
# Preenchendo valores nulos com base nas células anteriores
df['SETOR'].ffill(inplace=True)
df['SUBSETOR'].ffill(inplace=True)
df['SEGMENTO'].ffill(inplace=True)
# Removendo valores inconsistentes
df = df.loc[(df.CÓDIGO!='CÓDIGO') & (df.CÓDIGO!='LISTAGEM') & (~df.CÓDIGO.isnull())]
# Formatando todos os dados
df = df.apply(lambda x: x.str.strip() if x.dtype == 'object' else x)
# Alterando tipo das variáveis se necessário
df = df.apply(lambda x: x.astype('category') if (x.dtype == 'O') and (x.name not in ['CÓDIGO', 'NOME']) else x)
# Reordenando colunas
df = df[['CÓDIGO', 'NOME', 'SETOR', 'SUBSETOR', 'SEGMENTO', 'LISTAGEM']]
# Reiniciando indexs
df = df.reset_index(drop=True)
# Criando arquivo parquet para acessos posteriores
df.to_parquet(path='./tickers_por_setor.parquet')

# ANÁLISE EXPLORATÓRIA

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 432 entries, 0 to 431
Data columns (total 6 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   CÓDIGO    432 non-null    object  
 1   NOME      432 non-null    object  
 2   SETOR     432 non-null    category
 3   SUBSETOR  432 non-null    category
 4   SEGMENTO  432 non-null    category
 5   LISTAGEM  432 non-null    category
dtypes: category(4), object(2)
memory usage: 13.4+ KB


In [5]:
df.memory_usage()

Index        132
CÓDIGO      3456
NOME        3456
SETOR        820
SUBSETOR    1856
SEGMENTO    3200
LISTAGEM     804
dtype: int64

# ANÁLISE DESCRITIVA

- Qual a quantidade de papéis por setor?

In [6]:
dt = df.SETOR.value_counts(ascending=True)
fig = px.bar(data_frame=dt, y=dt.index, x=dt, template='plotly_dark', text_auto=True, title="Quantidade de papéis por setor", orientation='h')
fig.update_yaxes(title='QUANTIDADE')
fig.update_traces(hovertemplate=None)
fig.update_layout(hovermode='y')
fig.show()

Considerações:

    - x

- Qual a quantidade de papéis por setor, subsetor e segmento?

In [7]:
dt = df.value_counts(subset=['SETOR', 'SUBSETOR', 'SEGMENTO'], sort=False).reset_index()
fig = px.treemap(data_frame=dt, path=[px.Constant('Total'), 'SETOR', 'SUBSETOR', 'SEGMENTO'], values='count', template='plotly_dark')
fig.update_traces(hovertemplate=None)
fig.show()

c:\Users\adria\anaconda3\Lib\site-packages\plotly\express\_core.py:1619: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

c:\Users\adria\anaconda3\Lib\site-packages\plotly\express\_core.py:1619: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

c:\Users\adria\anaconda3\Lib\site-packages\plotly\express\_core.py:1619: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



Considerações:

    - x

- Qual a quantidade de papéis por tipo de listagem?

In [8]:
dt = df.LISTAGEM.value_counts()
fig = px.bar(data_frame=dt, x=dt.index, y=dt.values, template='plotly_dark', text_auto=True)
fig.update_traces(hovertemplate=None)
fig.update_layout(hovermode='x')
fig.show()

Considerações:

    - x